In [21]:
import h5py
from sklearn.model_selection import train_test_split

#now load this dataset 
h5f = h5py.File('./datasets/s8_sio2tio2_v2.h5','r')
X = h5f['sizes'][:]
Y = h5f['spectrum'][:]


#create a train - test split of the dataset
x_train, x_test, y_train, y_test = train_test_split(X, Y, test_size=0.4, random_state=42)

x_test = (x_test - 50.0)/20.0

x_test[9]


array([ 0.85, -0.95, -1.  , -0.65,  0.3 , -0.65,  0.55, -0.05])

In [2]:
import numpy as np
import mxnet as mx

# Step1: Load the model in MXNet

# Use the same prefix and epoch parameters we used in save_mxnet_model API.
sym, arg_params, aux_params = mx.model.load_checkpoint(prefix='my_mod', epoch=0)

# We use the data_names and data_shapes returned by save_mxnet_model API.
mod = mx.mod.Module(symbol=sym, 
                    data_names=['/input_12'], 
                    context=mx.gpu(), 
                    label_names=None)
mod.bind(for_training=False, 
         data_shapes=[('/input_12', (1,8))], 
         label_shapes=mod._label_shapes)
mod.set_params(arg_params, aux_params, allow_missing=True)                      

In [28]:
import scnets as scn
import mxnet as mx
from mxnet import nd
import time


bsize = 4000
y_true = nd.array(y_test[9], ctx=mx.gpu())
reps = 1000

start = time.time()
for icv in np.arange(reps):
    x_t = x_test[0:bsize]
    res2 = mod.predict(x_t)
    err = nd.abs(y_true - res2)/y_true
    finerr = 100*nd.mean(err)
end = time.time()
print(1000*(end - start))   

255.54943084716797


In [3]:
import scnets as scn
import mxnet as mx
from mxnet import nd
import time

size = np.random.randint(30, 71, (1,8))
#spec_ac = snlay.calc_spectrum(size, mats, lams)
size = (size - 50.0)/20.0
#size = np.expand_dims(size, axis = 0)
size.shape

y_true = nd.array(y_test[9], ctx=mx.gpu())

reps = 1000
start = time.time()
#res1 = model.predict(size)
#data_iter = mx.io.NDArrayIter(size, None, 1)
for icv in np.arange(reps):
    size = np.random.randint(30, 71, (1,8))
    size = (size - 50.0)/20.0
    res2 = mod.predict(size)
    err = nd.abs(y_true - res2)/y_true
    finerr = nd.sum(err)
    
end = time.time()
print(1000*(end - start)/reps)   

Using MXNet backend


0.17115497589111328


In [4]:
import scnets as scn
import mxnet as mx
from mxnet import nd
def give_loss(x_in, y_true, mxmod):
    y_t = nd.array(y_true, ctx=mx.gpu())
    res2 = mxmod.predict(x_in)
    err = nd.abs(y_t - res2)/y_t
    err2 = nd.sum(err).asscalar()
    #ez2 = err2.copyto(mx.cpu())
    return err2

#     err2cp = nd.zeros_like(err2, ctx=mx.cpu())

In [7]:
size = np.random.randint(30, 71, (1,8))
#spec_ac = snlay.calc_spectrum(size, mats, lams)
size = (size - 50.0)/20.0

ans = 1.00
cd = give_loss(x_in=size, y_true=y_test[6], mxmod=mod)


reps = 1000
start = time.time()
for icv in np.arange(reps):
    cc = give_loss(x_in=size, y_true=y_test[6], mxmod=mod)
    #ans = cc.asscalar()

end = time.time()
print(1000*(end - start)/reps)   # 

1.9373879432678223


In [6]:
cd

235.14212

In [124]:
x.__getitem__(0).asscalar()

1.0